# Westminster Ground Truth Analysis with MetaShape

This notebook demonstrates the complete workflow for creating orthomosaics from DJI drone imagery using **Agisoft MetaShape** and evaluating their accuracy:

1. **Data Loading**: Load images from three directories and GCPs from CSV
2. **DJI Metadata Processing**: Extract camera positions and orientations from nav, obs, bin, and MRK files
3. **GCP Conversion**: Convert UTM coordinates to WGS84 lat/lon for MetaShape
4. **Orthomosaic Creation**: Generate a single orthomosaic from ALL images with and without GCPs using MetaShape
5. **Basemap Comparison**: Download basemaps and quantify absolute accuracy
6. **Quality Report**: Generate comprehensive comparison report

## Datasets:
- **Directory 1**: DJI_202510060955_017_25-3288 (contains images, nav, obs, bin, MRK files)
- **Directory 2**: DJI_202510060955_018_25-3288 (contains images, nav, obs, bin, MRK files)
- **Directory 3**: DJI_202510060955_019_25-3288 (contains images, nav, obs, bin, MRK files)

**Ground Control Points**: 25-3288-CONTROL-NAD83-UTM10N-EGM2008.csv

We create a **single combined orthomosaic** from all images in all three directories:
- Orthomosaic **without** GCPs (using only image matching)
- Orthomosaic **with** GCPs (using image matching + ground control points)

Both orthomosaics are compared against reference basemaps to evaluate accuracy.


## Setup: Install Dependencies

First, install the required packages. Note: This notebook requires **Agisoft MetaShape Python API** to be installed separately.


In [1]:
# Install required packages
import subprocess
import sys
from pathlib import Path

# Try to install from requirements.txt first
requirements_file = Path("requirements.txt")
if requirements_file.exists():
    print("Installing packages from requirements.txt...")
    subprocess.check_call([sys.executable, "-m", "pip", "install", "-q", "-r", str(requirements_file)])
    print("✓ Packages installed from requirements.txt")
else:
    # Fallback: install packages individually
    print("requirements.txt not found. Installing packages individually...")
    packages = [
        "numpy>=1.24.0",
        "rasterio>=1.3.0",
        "pillow>=10.0.0",
        "matplotlib>=3.7.0",
        "pandas>=2.0.0",
        "pyproj>=3.6.0",
        "requests>=2.31.0",
        "utm>=0.7.0",
    ]
    for package in packages:
        subprocess.check_call([sys.executable, "-m", "pip", "install", "-q", package])
    print("✓ All packages installed")

# Check for MetaShape
try:
    import Metashape
    print("✓ MetaShape Python API is available")
    METASHAPE_AVAILABLE = True
except ImportError:
    print("⚠️  MetaShape Python API not found. Please install Agisoft MetaShape and its Python API.")
    print("   The API is typically installed with MetaShape at:")
    print("   - Windows: C:\\Program Files\\Agisoft\\Metashape Pro\\python")
    print("   - macOS: /Applications/Metashape Pro/Metashape.app/Contents/Frameworks/Python.framework/Versions/3.9")
    print("   - Linux: /opt/metashape-pro/lib/python3.9")
    METASHAPE_AVAILABLE = False

print("\nSetup complete!")


Installing packages from requirements.txt...
✓ Packages installed from requirements.txt
✓ MetaShape Python API is available

Setup complete!


## Imports


In [2]:
import sys
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
import warnings
import logging
import json
import csv
import xml.etree.ElementTree as ET
import utm
warnings.filterwarnings('ignore')

# Configure logging
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(name)s - %(levelname)s - %(message)s"
)

# Add package to path
sys.path.insert(0, str(Path.cwd()))

# Import Westminster-specific modules
from westminster_ground_truth_analysis import (
    GCPParser,
    download_basemap,
    compare_orthomosaic_to_basemap,
    DJIMetadataParser,
)

# Try to import MetaShape processor from qualicum_beach package
# If not available, we'll define the functions locally
try:
    from qualicum_beach_gcp_analysis import (
        process_orthomosaic,
        PhotoMatchQuality,
        DepthMapQuality,
        export_to_metashape_csv,
        export_to_metashape_xml,
    )
    print("✓ Using MetaShape processor from qualicum_beach_gcp_analysis")
    USE_QUALICUM_PACKAGE = True
except ImportError:
    print("⚠️  qualicum_beach_gcp_analysis not found. Will define MetaShape functions locally.")
    USE_QUALICUM_PACKAGE = False
    # We'll define these functions in the next cell if needed

# Set up paths
data_dir = Path("/Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25")
output_dir = Path("outputs")
output_dir.mkdir(exist_ok=True)

print("✓ Imports successful!")


✓ Using MetaShape processor from qualicum_beach_gcp_analysis
✓ Imports successful!


## Step 1: Load Ground Control Points


In [3]:
# Parse GCP file (UTM coordinates)
gcp_file = data_dir / "25-3288-CONTROL-NAD83-UTM10N-EGM2008.csv"
gcp_parser = GCPParser(str(gcp_file))

gcps_utm = gcp_parser.get_gcps()
print(f"Loaded {len(gcps_utm)} ground control points (UTM format)")

# Display first few GCPs
print("\nFirst few GCPs (UTM):")
for gcp in gcps_utm[:5]:
    print(f"  {gcp.name}: X={gcp.x:.2f}, Y={gcp.y:.2f}, Z={gcp.z:.2f}")

# Get bounds
min_x, min_y, max_x, max_y = gcp_parser.get_bounds()
print(f"\nGCP Bounds (UTM): X=[{min_x:.2f}, {max_x:.2f}], Y=[{min_y:.2f}, {max_y:.2f}]")


Loaded 23 ground control points (UTM format)

First few GCPs (UTM):
  GCP1: X=5450945.53, Y=506914.12, Z=77.45
  GCP2: X=5450730.01, Y=506657.79, Z=79.22
  GCP3: X=5450480.01, Y=506577.77, Z=59.40
  GCP4: X=5450578.63, Y=506765.03, Z=65.59
  GCP5: X=5450715.96, Y=506926.13, Z=63.10

GCP Bounds (UTM): X=[5450109.82, 5450992.66], Y=[506577.77, 507315.01]


## Step 2: Process DJI Metadata from All Directories

Each directory contains nav, obs, bin, and MRK files that provide camera positions, orientations, and timestamps. We'll parse these to potentially enhance the processing.


In [4]:
# Process DJI metadata from all three directories
dataset_dirs = [
    data_dir / "DJI_202510060955_017_25-3288",
    data_dir / "DJI_202510060955_018_25-3288",
    data_dir / "DJI_202510060955_019_25-3288",
]

dji_metadata_parsers = {}
total_images = 0

for dataset_dir in dataset_dirs:
    if dataset_dir.exists():
        print(f"\n📂 Processing metadata from: {dataset_dir.name}")
        try:
            parser = DJIMetadataParser(str(dataset_dir))
            dji_metadata_parsers[dataset_dir.name] = parser
            
            # Count images in this directory
            images = list(dataset_dir.glob("*.jpg")) + list(dataset_dir.glob("*.JPG"))
            total_images += len(images)
            
            print(f"  ✓ Parsed {len(parser.timestamps)} timestamps")
            print(f"  ✓ Parsed {len(parser.nav_data)} navigation entries")
            print(f"  ✓ Found {len(images)} images")
        except Exception as e:
            print(f"  ⚠️  Error processing metadata: {e}")
    else:
        print(f"  ⚠️  Directory not found: {dataset_dir}")

print(f"\n✓ Total images across all directories: {total_images}")
print(f"✓ Processed metadata from {len(dji_metadata_parsers)} directories")



📂 Processing metadata from: DJI_202510060955_017_25-3288
Parsing timestamp file: /Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25/DJI_202510060955_017_25-3288/DJI_202510060955_017_25-3288_Timestamp.MRK
Parsing navigation file: /Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25/DJI_202510060955_017_25-3288/DJI_202510060955_017_25-3288_PPKNAV.nav
  ✓ Parsed 0 timestamps
  ✓ Parsed 0 navigation entries
  ✓ Found 543 images

📂 Processing metadata from: DJI_202510060955_018_25-3288
Parsing timestamp file: /Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25/DJI_202510060955_018_25-3288/DJI_202510060955_018_25-3288_Timestamp.MRK
Parsing navigation file: /Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25/DJI_202510060955_018_25-3288/DJI_202510060955_018_25-3288_PPKNAV.nav
  ✓ Parsed 0 timestamps
  ✓ Parsed 0 navigation entries
  ✓ Found 865 images

📂 Processing metadata from: DJI_202510060955_019_25-3288
Parsing time

## Step 3: Convert GCPs to WGS84 Lat/Lon for MetaShape

MetaShape expects GCPs in WGS84 lat/lon format. We need to convert from UTM Zone 10N.


In [5]:
# Convert UTM to WGS84 lat/lon
# NOTE: In the CSV, X column is actually Northing (~5.45M) and Y column is Easting (~500k)
# utm.to_latlon expects (easting, northing), so we need to swap them
gcps_wgs84 = []

for gcp in gcps_utm:
    # Convert UTM to lat/lon (UTM Zone 10N)
    # X is Northing, Y is Easting
    lat, lon = utm.to_latlon(gcp.y, gcp.x, 10, 'N')
    
    gcp_dict = {
        'id': gcp.name,
        'label': gcp.name,
        'lat': lat,
        'lon': lon,
        'z': gcp.z,
        'accuracy': 0.1  # Default accuracy in meters
    }
    gcps_wgs84.append(gcp_dict)

print(f"Converted {len(gcps_wgs84)} GCPs to WGS84 lat/lon")
print("\nFirst few GCPs (WGS84):")
for gcp in gcps_wgs84[:5]:
    print(f"  {gcp['id']}: ({gcp['lat']:.6f}, {gcp['lon']:.6f}, z={gcp['z']:.2f})")


Converted 23 GCPs to WGS84 lat/lon

First few GCPs (WGS84):
  GCP1: (49.211262, -122.905068, z=77.45)
  GCP2: (49.209326, -122.908591, z=79.22)
  GCP3: (49.207078, -122.909694, z=59.40)
  GCP4: (49.207963, -122.907122, z=65.59)
  GCP5: (49.209197, -122.904907, z=63.10)


## Step 4: Export GCPs for MetaShape


In [6]:
# Create output directory for GCP files
gcp_output_dir = output_dir / "gcps"
gcp_output_dir.mkdir(exist_ok=True)

# Export to MetaShape XML format (preferred by MetaShape)
if USE_QUALICUM_PACKAGE:
    gcp_xml_path = gcp_output_dir / "gcps_metashape.xml"
    export_to_metashape_xml(gcps_wgs84, str(gcp_xml_path))
    print(f"✓ GCPs exported to XML: {gcp_xml_path}")
    
    # Also export CSV for reference
    gcp_csv_path = gcp_output_dir / "gcps_metashape.csv"
    export_to_metashape_csv(gcps_wgs84, str(gcp_csv_path))
    print(f"✓ GCPs also exported to CSV: {gcp_csv_path}")
else:
    # Define export functions locally if qualicum package not available
    def export_to_metashape_xml_local(gcps, output_path):
        output_path = Path(output_path)
        output_path.parent.mkdir(parents=True, exist_ok=True)
        
        root = ET.Element('document')
        chunks = ET.SubElement(root, 'chunks')
        chunk = ET.SubElement(chunks, 'chunk')
        markers = ET.SubElement(chunk, 'markers')
        
        for gcp in gcps:
            marker = ET.SubElement(markers, 'marker')
            marker.set('label', gcp.get('id', gcp.get('label', 'GCP')))
            marker.set('reference', 'true')
            
            position = ET.SubElement(marker, 'position')
            position.set('x', str(gcp.get('lon', 0.0)))
            position.set('y', str(gcp.get('lat', 0.0)))
            position.set('z', str(gcp.get('z', 0.0)))
            
            accuracy = gcp.get('accuracy', 1.0)
            accuracy_elem = ET.SubElement(marker, 'accuracy')
            accuracy_elem.set('x', str(accuracy))
            accuracy_elem.set('y', str(accuracy))
            accuracy_elem.set('z', str(accuracy))
        
        tree = ET.ElementTree(root)
        ET.indent(tree, space='  ')
        tree.write(output_path, encoding='utf-8', xml_declaration=True)
        print(f"Exported {len(gcps)} GCPs to MetaShape XML: {output_path}")
        return str(output_path)
    
    def export_to_metashape_csv_local(gcps, output_path):
        output_path = Path(output_path)
        output_path.parent.mkdir(parents=True, exist_ok=True)
        
        with open(output_path, 'w', newline='') as f:
            writer = csv.writer(f, delimiter='\t')
            writer.writerow(['Label', 'X', 'Y', 'Z', 'Accuracy', 'Enabled'])
            
            for gcp in gcps:
                label = gcp.get('id', gcp.get('label', 'GCP'))
                lon = gcp.get('lon', 0.0)
                lat = gcp.get('lat', 0.0)
                z = gcp.get('z', 0.0)
                # Use very low accuracy (0.01m = 1cm) for high weight in MetaShape bundle adjustment
                # Lower accuracy values = higher weight in bundle adjustment
                accuracy = gcp.get('accuracy', 0.01)
                writer.writerow([label, lon, lat, z, accuracy, '1'])
        
        print(f"Exported {len(gcps)} GCPs to MetaShape CSV: {output_path}")
        return str(output_path)
    
    gcp_xml_path = gcp_output_dir / "gcps_metashape.xml"
    export_to_metashape_xml_local(gcps_wgs84, str(gcp_xml_path))
    print(f"✓ GCPs exported to XML: {gcp_xml_path}")
    
    gcp_csv_path = gcp_output_dir / "gcps_metashape.csv"
    export_to_metashape_csv_local(gcps_wgs84, str(gcp_csv_path))
    print(f"✓ GCPs also exported to CSV: {gcp_csv_path}")

# Use CSV file for processing (more reliable than XML)
# If CSV doesn't exist, fall back to XML
if gcp_csv_path.exists():
    gcp_file_for_processing = gcp_csv_path
    print(f"✓ Using CSV format for GCP import: {gcp_csv_path}")
else:
    gcp_file_for_processing = gcp_xml_path
    print(f"✓ Using XML format for GCP import: {gcp_xml_path}")

# Use CSV file for processing (more reliable than XML)
# If CSV doesn't exist, fall back to XML
if gcp_csv_path.exists():
    gcp_file_for_processing = gcp_csv_path
    print(f"✓ Using CSV format for GCP import: {gcp_csv_path}")
else:
    gcp_file_for_processing = gcp_xml_path
    print(f"✓ Using XML format for GCP import: {gcp_xml_path}")


Exported 23 GCPs to MetaShape XML: outputs/gcps/gcps_metashape.xml
✓ GCPs exported to XML: outputs/gcps/gcps_metashape.xml
Exported 23 GCPs to MetaShape CSV: outputs/gcps/gcps_metashape.csv
✓ GCPs also exported to CSV: outputs/gcps/gcps_metashape.csv
✓ Using CSV format for GCP import: outputs/gcps/gcps_metashape.csv
✓ Using CSV format for GCP import: outputs/gcps/gcps_metashape.csv


In [ ]:
# Define MetaShape processing functions if qualicum package not available
# USE_STANDARD_PIPELINE_PARAMETERS indicates if we're using the qualicum package's standard pipeline
# If not available, we define the functions locally with the same parameters
try:
    USE_STANDARD_PIPELINE_PARAMETERS = USE_QUALICUM_PACKAGE
except NameError:
    USE_STANDARD_PIPELINE_PARAMETERS = False

# Check if MetaShape is available (defined in setup cell)
try:
    _ = METASHAPE_AVAILABLE
except NameError:
    METASHAPE_AVAILABLE = False

if not USE_STANDARD_PIPELINE_PARAMETERS and METASHAPE_AVAILABLE:
    from enum import IntEnum
    from typing import Optional
    from contextlib import contextmanager
    
    class PhotoMatchQuality(IntEnum):
        LowestQuality = 0
        LowQuality = 1
        MediumQuality = 2
        HighQuality = 4
        HighestQuality = 8
    
    class DepthMapQuality(IntEnum):
        LowestQuality = 1
        LowQuality = 2
        MediumQuality = 4
        HighQuality = 8
        UltraQuality = 16
    
    @contextmanager
    def redirect_metashape_output(log_file_path: Path):
        """Context manager to redirect MetaShape's stdout/stderr to a log file.
        
        MetaShape prints verbose output to stdout/stderr. This function redirects
        that output to a log file while keeping minimal progress info in the notebook.
        """
        log_file_path.parent.mkdir(parents=True, exist_ok=True)
        # Open in write mode to start fresh each time (or append if you want to keep history)
        log_file = open(log_file_path, 'w', encoding='utf-8')
        original_stdout = sys.stdout
        original_stderr = sys.stderr
        
        # Create a Tee-like object that writes to both file and original stdout for progress
        class TeeOutput:
            def __init__(self, file, original):
                self.file = file
                self.original = original
                self.buffer = []
            
            def write(self, text):
                # Always write to log file
                self.file.write(text)
                self.file.flush()  # Flush immediately so log file is up to date
                
                # Only show minimal progress in notebook (filter verbose output)
                # MetaShape progress lines typically contain "Progress:" or percentages
                if any(keyword in text for keyword in ['Progress:', '%', '✓', '✗', '⚠️', '📝', '📂', '📷', '🔍', '📐', '🗺️', '🏗️', '🖼️', '💾']):
                    # Show progress indicators in notebook
                    self.original.write(text)
                    self.original.flush()
                # Suppress verbose technical output in notebook
            
            def flush(self):
                self.file.flush()
                self.original.flush()
        
        tee_stdout = TeeOutput(log_file, original_stdout)
        tee_stderr = TeeOutput(log_file, original_stderr)
        
        try:
            sys.stdout = tee_stdout
            sys.stderr = tee_stderr
            yield log_file
        finally:
            sys.stdout = original_stdout
            sys.stderr = original_stderr
            log_file.flush()
            log_file.close()
    
    def process_orthomosaic(
        photos_dir: Path,
        output_path: Path,
        project_path: Path,
        gcp_file: Optional[Path] = None,
        product_id: str = "orthomosaic",
        clean_intermediate_files: bool = False,
        photo_match_quality: int = PhotoMatchQuality.MediumQuality,
        depth_map_quality: int = DepthMapQuality.MediumQuality,
        tiepoint_limit: int = 10000,
        use_gcps: bool = False
    ) -> dict:
        """Process orthomosaic using MetaShape with output redirected to log file."""
        import Metashape
        
        # Configure GPU
        Metashape.app.gpu_mask = ~0
        
        # Setup paths
        output_path.mkdir(parents=True, exist_ok=True)
        project_path.parent.mkdir(parents=True, exist_ok=True)
        
        # Setup log file for MetaShape verbose output
        log_dir = project_path.parent / "logs"
        log_dir.mkdir(parents=True, exist_ok=True)
        log_file_path = log_dir / f"{product_id}_metashape.log"
        
        print(f"📝 MetaShape verbose output will be saved to: {log_file_path}")
        
        # Check if project exists
        project_exists = project_path.exists()
        
        # Helper function to safely save document
        def safe_save_document():
            """Save document, handling read-only errors by recreating the document."""
            nonlocal doc, chunk
            try:
                doc.save(str(project_path))
            except OSError as e:
                if "read-only" in str(e).lower() or "editing is disabled" in str(e).lower():
                    print(f"  ⚠️  Document became read-only, recreating...")
                    # Close the read-only document
                    try:
                        doc.close()
                    except:
                        pass
                    # Create a new writable document and copy the chunk data
                    # Note: We can't easily copy chunk data, so we'll just create a new document
                    # This means we lose the current processing state, but at least we can continue
                    print(f"  ⚠️  Warning: Processing state may be lost. Consider using clean_intermediate_files=True next time.")
                    doc = Metashape.Document()
                    doc.save(str(project_path))
                    # Get the chunk from the new document
                    if len(doc.chunks) > 0:
                        chunk = doc.chunks[0]
                    else:
                        chunk = doc.addChunk()
                else:
                    raise
        
        # Use context manager to redirect MetaShape output to log file
        with redirect_metashape_output(log_file_path):
            # Close any existing document first to avoid "already in use" error
            try:
                # Close all open documents
                if hasattr(Metashape.app, 'document') and Metashape.app.document is not None:
                    Metashape.app.document.close()
                # Also try to close via app.documents if available
                if hasattr(Metashape.app, 'documents'):
                    for d in list(Metashape.app.documents):
                        try:
                            d.close()
                        except:
                            pass
            except:
                pass  # Ignore errors when closing
            
            doc = None
            if project_exists and not clean_intermediate_files:
                print(f"📂 Loading existing project: {project_path}")
                doc = Metashape.Document()
                try:
                    doc.open(str(project_path))
                    # Check if document is read-only - if so, we need to close and recreate
                    # Try a test save to see if it's writable
                    try:
                        doc.save(str(project_path))
                        doc_readonly = False
                    except OSError as e:
                        if "read-only" in str(e).lower() or "editing is disabled" in str(e).lower():
                            print(f"  ⚠️  Document is read-only, closing and creating new project...")
                            doc.close()
                            doc = None
                            doc_readonly = True
                        else:
                            raise
                    
                    if doc is not None and not doc_readonly:
                        if len(doc.chunks) > 0:
                            chunk = doc.chunks[0]
                            print(f"  ✓ Found existing chunk with {len(chunk.cameras)} cameras")
                        else:
                            chunk = doc.addChunk()
                            print("  ✓ Created new chunk")
                except Exception as e:
                    # If open fails (e.g., file locked), try to create new project
                    print(f"  ⚠️  Could not open existing project: {e}")
                    print("  Creating new project instead...")
                    if doc is not None:
                        try:
                            doc.close()
                        except:
                            pass
                    doc = None
            
            # Create new document if we don't have one yet
            if doc is None:
                if clean_intermediate_files and project_exists:
                    try:
                        project_path.unlink()
                    except:
                        pass  # Ignore if can't delete
                print("🚀 Creating new MetaShape project...")
                doc = Metashape.Document()
                doc.save(str(project_path))
                chunk = doc.addChunk()
            
            # Add photos
            if len(chunk.cameras) == 0:
                print(f"📷 Adding photos from: {photos_dir}")
                photos = list(photos_dir.glob("*.jpg")) + list(photos_dir.glob("*.JPG"))
                if not photos:
                    raise ValueError(f"No images found in {photos_dir}")
                chunk.addPhotos([str(p) for p in photos])
                safe_save_document()  # Save after adding photos
                print(f"  ✓ Added {len(photos)} photos")
            else:
                print(f"  ✓ Photos already added ({len(chunk.cameras)} cameras)")
            
            # Add GCPs if requested
            if use_gcps and gcp_file and gcp_file.exists():
                if len(chunk.markers) == 0:
                    print(f"📍 Loading GCPs from: {gcp_file}")
                    
                    # Check file extension to determine format
                    file_ext = Path(gcp_file).suffix.lower()
                    markers_added = 0
                    
                    if file_ext == '.xml':
                        # Try XML format first
                        try:
                            chunk.importMarkers(str(gcp_file))
                            markers_added = len(chunk.markers)
                            print(f"  ✓ Added {markers_added} markers from XML")
                        except Exception as e:
                            print(f"  ⚠️  XML import failed: {e}")
                            print(f"  Trying CSV format instead...")
                            # Fall back to CSV if XML fails
                            file_ext = '.csv'
                    
                    if file_ext == '.csv' or file_ext == '.txt':
                        # CSV format - read and add markers manually
                        import csv
                        with open(gcp_file, 'r', encoding='utf-8') as f:
                            reader = csv.DictReader(f, delimiter='\t')
                            for row in reader:
                                try:
                                    label = row.get('Label', row.get('label', ''))
                                    x = float(row.get('X', row.get('x', 0)))
                                    y = float(row.get('Y', row.get('y', 0)))
                                    z = float(row.get('Z', row.get('z', 0)))
                                    accuracy = float(row.get('Accuracy', row.get('accuracy', 1.0)))
                                    enabled = row.get('Enabled', row.get('enabled', '1')).strip() == '1'
                                    
                                    # Create marker
                                    marker = chunk.addMarker()
                                    marker.label = label
                                    marker.reference.location = Metashape.Vector([x, y, z])
                                    marker.reference.accuracy = Metashape.Vector([accuracy, accuracy, accuracy])
                                    marker.reference.enabled = enabled
                                    markers_added += 1
                                except Exception as e:
                                    print(f"  ⚠️  Error adding marker from row: {e}")
                                    continue
                        
                        if markers_added > 0:
                            print(f"  ✓ Added {markers_added} markers from CSV")
                        else:
                            raise ValueError(f"Failed to add any markers from {gcp_file}")
                    
                    safe_save_document()  # Save after adding GCPs
                    print(f"  ✓ Total markers: {len(chunk.markers)}")
                else:
                    print(f"  ✓ GCPs already loaded ({len(chunk.markers)} markers)")
            
            # Match photos
            # Check if tie points exist - MetaShape TiePoints object may not support len()
            # Also check if cameras are already aligned (which requires tie points)
            tie_points_exist = chunk.tie_points is not None
            cameras_aligned = sum(1 for cam in chunk.cameras if cam.transform) > 0
            
            # If cameras are aligned, we definitely have tie points (even if we can't count them)
            if cameras_aligned:
                tie_points_exist = True
                tie_points_count = 1  # Don't need exact count, just know they exist
            elif tie_points_exist:
                # Try to get count, but handle case where len() doesn't work on TiePoints object
                try:
                    tie_points_count = len(chunk.tie_points)
                except (TypeError, AttributeError):
                    # If len() doesn't work, check if we can iterate or get a count attribute
                    try:
                        # Try to get point count if available
                        tie_points_count = chunk.tie_points.point_count if hasattr(chunk.tie_points, 'point_count') else None
                        if tie_points_count is None:
                            # Try to check if it's iterable and count items
                            try:
                                tie_points_count = sum(1 for _ in chunk.tie_points)
                            except:
                                tie_points_count = 1  # Assume it has points if it exists
                    except:
                        tie_points_count = 1  # Assume it has points if it exists
            else:
                tie_points_count = 0
            
            if not tie_points_exist or tie_points_count == 0:
                print("🔍 Matching photos... (this may take a while)")
                chunk.matchPhotos(
                    downscale=photo_match_quality,
                    tiepoint_limit=tiepoint_limit,
                )
                safe_save_document()  # Save after matching photos
                # Try to get count after matching
                if chunk.tie_points is not None:
                    try:
                        tie_points_count = len(chunk.tie_points)
                    except (TypeError, AttributeError):
                        try:
                            tie_points_count = chunk.tie_points.point_count if hasattr(chunk.tie_points, 'point_count') else 0
                        except:
                            try:
                                tie_points_count = sum(1 for _ in chunk.tie_points)
                            except:
                                tie_points_count = 0
                else:
                    tie_points_count = 0
                print(f"  ✓ Photo matching complete ({tie_points_count} tie points)")
            else:
                print(f"  ✓ Photos already matched ({tie_points_count} tie points)")
            
            # Align cameras
            aligned = sum(1 for cam in chunk.cameras if cam.transform)
            cameras_aligned = aligned > 0
            if aligned == 0:
                print("📐 Aligning cameras... (this may take a while)")
                chunk.alignCameras()
                safe_save_document()
                aligned = sum(1 for cam in chunk.cameras if cam.transform)
                cameras_aligned = aligned > 0
                print(f"  ✓ Camera alignment complete ({aligned}/{len(chunk.cameras)} cameras aligned)")
            else:
                print(f"  ✓ Cameras already aligned ({aligned}/{len(chunk.cameras)} cameras)")
            
            # Build depth maps
            # Check if depth maps exist - cameras must be aligned first
            # DepthMaps object doesn't support len(), so just check if it exists
            if not cameras_aligned:
                print("  ⚠️  Skipping depth maps - cameras not aligned yet")
                depth_maps_exist = False
            else:
                depth_maps_exist = chunk.depth_maps is not None
                if not depth_maps_exist:
                    print("🗺️  Building depth maps... (this may take a while)")
                    chunk.buildDepthMaps(
                        downscale=depth_map_quality,
                        filter_mode=Metashape.MildFiltering
                    )
                    safe_save_document()  # Save after building depth maps
                    depth_maps_exist = chunk.depth_maps is not None
                    if depth_maps_exist:
                        # Try to get count for display, but handle if len() doesn't work
                        try:
                            depth_maps_count = len(chunk.depth_maps)
                        except (TypeError, AttributeError):
                            # Try alternative methods to get count
                            try:
                                depth_maps_count = chunk.depth_maps.count if hasattr(chunk.depth_maps, 'count') else None
                            except:
                                depth_maps_count = None
                            if depth_maps_count is None:
                                try:
                                    depth_maps_count = sum(1 for _ in chunk.depth_maps)
                                except:
                                    depth_maps_count = "?"
                        print(f"  ✓ Depth maps built ({depth_maps_count} depth maps)" if depth_maps_count != "?" else "  ✓ Depth maps built")
                    else:
                        print("  ⚠️  Depth map building may have failed")
                else:
                    # Try to get count for display
                    try:
                        depth_maps_count = len(chunk.depth_maps)
                    except (TypeError, AttributeError):
                        try:
                            depth_maps_count = chunk.depth_maps.count if hasattr(chunk.depth_maps, 'count') else "?"
                        except:
                            depth_maps_count = "?"
                        if depth_maps_count == "?":
                            try:
                                depth_maps_count = sum(1 for _ in chunk.depth_maps)
                            except:
                                depth_maps_count = "?"
                    print(f"  ✓ Depth maps already built ({depth_maps_count} depth maps)" if depth_maps_count != "?" else "  ✓ Depth maps already built")
            
            # Build model
            # Model requires depth maps
            if not depth_maps_exist:
                print("  ⚠️  Skipping model - depth maps not built yet")
            elif chunk.model is None:
                print("🏗️  Building 3D model... (this may take a while)")
                chunk.buildModel()
                safe_save_document()  # Save after building model
                print("  ✓ 3D model built")
            else:
                print("  ✓ 3D model already built")
            
            # Build orthomosaic
            # Orthomosaic requires model
            if chunk.model is None:
                print("  ⚠️  Skipping orthomosaic - model not built yet")
            elif chunk.orthomosaic is None:
                print("🖼️  Building orthomosaic... (this may take a while)")
                chunk.buildOrthomosaic()
                safe_save_document()  # Save after building orthomosaic
                print("  ✓ Orthomosaic built")
            else:
                print("  ✓ Orthomosaic already built")
            
            # Export GeoTIFF with LZW compression (lossless, reduces file size by 30-50%)
            ortho_path = output_path / f"{product_id}.tif"
            if not ortho_path.exists() or clean_intermediate_files:
                print(f"💾 Exporting GeoTIFF to: {ortho_path}")
                compression = Metashape.ImageCompression()
                compression.tiff_compression = Metashape.ImageCompression.TiffCompressionLZW  # Use LZW for compression
                compression.tiff_big = True
                compression.tiff_overviews = True
                compression.tiff_tiled = True
                chunk.exportRaster(str(ortho_path), image_compression=compression)
                safe_save_document()
                if ortho_path.exists():
                    file_size_mb = ortho_path.stat().st_size / (1024 * 1024)
                    print(f"  ✓ GeoTIFF exported ({file_size_mb:.2f} MB)")
                else:
                    print(f"  ⚠️  Export completed but file not found at: {ortho_path}")
            else:
                file_size_mb = ortho_path.stat().st_size / (1024 * 1024)
                print(f"  ✓ GeoTIFF already exists ({file_size_mb:.2f} MB)")
        
        stats = {
            'product_id': product_id,
            'use_gcps': use_gcps,
            'num_photos': len(chunk.cameras),
            'num_markers': len(chunk.markers),
            'ortho_path': str(ortho_path),
            'project_path': str(project_path),
            'log_file_path': str(log_file_path),
        }
        
        print(f"\n✅ Processing complete! Log file: {log_file_path}")
        return stats
    
    print("✓ MetaShape processing functions defined locally")
elif not METASHAPE_AVAILABLE:
    print("⚠️  MetaShape not available. Cannot process orthomosaics.")
else:
    print("✓ Using MetaShape processor from qualicum_beach_gcp_analysis")


✓ Using MetaShape processor from qualicum_beach_gcp_analysis


In [ ]:
# Check if METASHAPE_AVAILABLE is defined (from setup cell)
try:
    _ = METASHAPE_AVAILABLE
except NameError:
    METASHAPE_AVAILABLE = False
    print("⚠️  METASHAPE_AVAILABLE not defined. Assuming MetaShape is not available.")
    print("   Please run the setup cell first to check for MetaShape installation.")

if not METASHAPE_AVAILABLE:
    print("⚠️  MetaShape not available. Skipping processing.")
else:
    # Flag to control whether to compute non-GCP case (set to False to skip, saves time)
    COMPUTE_NON_GCP_CASE = False  # Set to True to compute orthomosaic without GCPs
    
    # Setup paths
    intermediate_dir = output_dir / "intermediate"
    ortho_output_dir = output_dir / "orthomosaics"
    
    # Process orthomosaic WITHOUT GCPs (if flag is enabled)
    if COMPUTE_NON_GCP_CASE:
        print("=" * 60)
        print("Processing Combined Orthomosaic - WITHOUT GCPs...")
        print("=" * 60)
        print(f"Combining images from:")
        # Define data_dir if not already defined
        try:
            _ = data_dir
        except NameError:
            # Default data directory path
            data_dir = Path("/Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25")
            print(f"ℹ️  data_dir not defined, using default: {data_dir}")
        
        # Define dataset_dirs if not already defined (from Step 2)
        try:
            _ = dataset_dirs
        except NameError:
            # Define the three dataset directories
            dataset_dirs = [
                data_dir / "DJI_202510060955_017_25-3288",
                data_dir / "DJI_202510060955_018_25-3288",
                data_dir / "DJI_202510060955_019_25-3288",
            ]
            print("ℹ️  dataset_dirs not defined, using default paths from Step 2")
        
        for dataset_dir in dataset_dirs:
            if dataset_dir.exists():
                images = list(dataset_dir.glob("*.jpg")) + list(dataset_dir.glob("*.JPG"))
                print(f"  - {dataset_dir.name}: {len(images)} images")
        
        project_path_no_gcps = intermediate_dir / "combined_no_gcps.psx"
        
        # When using qualicum package, create temporary combined directory
        if USE_QUALICUM_PACKAGE:
            import tempfile
            import shutil
            from pathlib import Path
            
            # Create temporary directory for combined images
            temp_combined_dir = Path(tempfile.mkdtemp(prefix="combined_images_"))
            print(f"📁 Created temporary combined directory: {temp_combined_dir}")
            
            # Collect all images from all directories and create symlinks
            total_images = 0
            for dataset_dir in dataset_dirs:
                if dataset_dir.exists():
                    images = list(dataset_dir.glob("*.jpg")) + list(dataset_dir.glob("*.JPG"))
                    for img_path in images:
                        # Create symlink in temp directory
                        symlink_path = temp_combined_dir / img_path.name
                        # Handle name conflicts by including parent dir name
                        if symlink_path.exists():
                            symlink_path = temp_combined_dir / f"{dataset_dir.name}_{img_path.name}"
                        symlink_path.symlink_to(img_path.resolve())
                        total_images += 1
            
            print(f"  ✓ Created {total_images} symlinks in temporary directory")
            photos_dir_for_qualicum = temp_combined_dir
        else:
            photos_dir_for_qualicum = dataset_dirs
        
        if USE_QUALICUM_PACKAGE:
            stats_no_gcps = process_orthomosaic(
                photos_dir=photos_dir_for_qualicum,
                output_path=ortho_output_dir,
                project_path=project_path_no_gcps,
                product_id="combined_no_gcps",
                clean_intermediate_files=False,
                photo_match_quality=PhotoMatchQuality.MediumQuality,
                depth_map_quality=DepthMapQuality.MediumQuality,
                tiepoint_limit=10000,
                use_gcps=False
            )
        else:
            stats_no_gcps = process_orthomosaic(
                photos_dir=dataset_dirs,
                output_path=ortho_output_dir,
                project_path=project_path_no_gcps,
                product_id="combined_no_gcps",
                clean_intermediate_files=False,
                photo_match_quality=PhotoMatchQuality.MediumQuality,
                depth_map_quality=DepthMapQuality.MediumQuality,
                tiepoint_limit=10000,
                use_gcps=False
            )
        
        print("\n✓ Combined orthomosaic processing (without GCPs) complete!")
        print(f"  Number of photos: {stats_no_gcps['num_photos']}")
        print(f"  Orthomosaic: {stats_no_gcps['ortho_path']}")
        
        ortho_no_gcps_path = Path(stats_no_gcps['ortho_path'])
        
        # Post-processing: Compress existing large GeoTIFF files if they're not already compressed
        if ortho_no_gcps_path.exists():
            file_size_gb = ortho_no_gcps_path.stat().st_size / (1024 * 1024 * 1024)
            if file_size_gb > 1.0:  # If file is larger than 1GB, try to compress
                print(f"\n📦 File size is {file_size_gb:.2f} GB. Attempting post-processing compression...")
                try:
                    import rasterio
                    from rasterio.enums import Compression
                    
                    # Read the file
                    with rasterio.open(ortho_no_gcps_path, 'r') as src:
                        data = src.read()
                        profile = src.profile.copy()
                    
                    # Update profile with LZW compression
                    profile.update({
                        'compress': 'lzw',
                        'tiled': True,
                        'blockxsize': 512,
                        'blockysize': 512,
                    })
                    
                    # Write compressed version to temporary file
                    temp_path = ortho_no_gcps_path.with_suffix('.tif.tmp')
                    with rasterio.open(temp_path, 'w', **profile) as dst:
                        dst.write(data)
                    
                    # Replace original with compressed version
                    temp_path.replace(ortho_no_gcps_path)
                    new_size_gb = ortho_no_gcps_path.stat().st_size / (1024 * 1024 * 1024)
                    compression_ratio = (1 - new_size_gb / file_size_gb) * 100
                    print(f"  ✓ Compression complete: {file_size_gb:.2f} GB → {new_size_gb:.2f} GB ({compression_ratio:.1f}% reduction)")
                except Exception as e:
                    print(f"  ⚠️  Post-processing compression failed: {e}")
                    print(f"  Note: File was exported with LZW compression from MetaShape, so it should already be compressed.")
    else:
        print("ℹ️  Skipping non-GCP case (COMPUTE_NON_GCP_CASE=False). Set to True to compute.")
        ortho_no_gcps_path = ortho_output_dir / "combined_no_gcps.tif"
    
    # Process orthomosaic WITH GCPs (using all three directories)
    print("=" * 60)
    print("Processing Combined Orthomosaic - WITH GCPs...")
    print("=" * 60)
    print(f"Combining images from:")
    # Define data_dir if not already defined
    try:
        _ = data_dir
    except NameError:
        # Default data directory path
        data_dir = Path("/Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25")
        print(f"ℹ️  data_dir not defined, using default: {data_dir}")
    
    # Define dataset_dirs if not already defined (from Step 2)
    try:
        _ = dataset_dirs
    except NameError:
        # Define the three dataset directories
        dataset_dirs = [
            data_dir / "DJI_202510060955_017_25-3288",
            data_dir / "DJI_202510060955_018_25-3288",
            data_dir / "DJI_202510060955_019_25-3288",
        ]
        print("ℹ️  dataset_dirs not defined, using default paths from Step 2")
    
    for dataset_dir in dataset_dirs:
        if dataset_dir.exists():
            images = list(dataset_dir.glob("*.jpg")) + list(dataset_dir.glob("*.JPG"))
            print(f"  - {dataset_dir.name}: {len(images)} images")
    
    project_path_with_gcps = intermediate_dir / "combined_with_gcps.psx"
    
    # When using qualicum package, create temporary combined directory
    # since it expects a single directory, not a list
    if USE_QUALICUM_PACKAGE:
        import tempfile
        import shutil
        from pathlib import Path
        
        # Create temporary directory for combined images
        temp_combined_dir = Path(tempfile.mkdtemp(prefix="combined_images_"))
        print(f"📁 Created temporary combined directory: {temp_combined_dir}")
        
        # Collect all images from all directories and create symlinks
        total_images = 0
        for dataset_dir in dataset_dirs:
            if dataset_dir.exists():
                images = list(dataset_dir.glob("*.jpg")) + list(dataset_dir.glob("*.JPG"))
                for img_path in images:
                    # Create symlink in temp directory
                    symlink_path = temp_combined_dir / img_path.name
                    # Handle name conflicts by including parent dir name
                    if symlink_path.exists():
                        symlink_path = temp_combined_dir / f"{dataset_dir.name}_{img_path.name}"
                    symlink_path.symlink_to(img_path.resolve())
                    total_images += 1
        
        print(f"  ✓ Created {total_images} symlinks in temporary directory")
        photos_dir_for_qualicum = temp_combined_dir
    else:
        photos_dir_for_qualicum = dataset_dirs
    
    if USE_QUALICUM_PACKAGE:
        stats_with_gcps = process_orthomosaic(
            photos_dir=photos_dir_for_qualicum,
            output_path=ortho_output_dir,
            project_path=project_path_with_gcps,
            gcp_file=gcp_file_for_processing,
            product_id="combined_with_gcps",
            clean_intermediate_files=False,
            photo_match_quality=PhotoMatchQuality.MediumQuality,
            depth_map_quality=DepthMapQuality.MediumQuality,
            tiepoint_limit=10000,
            use_gcps=True,
            gcp_accuracy=0.01  # Very low accuracy (1cm) for very high weight in bundle adjustment
        )
    else:
        stats_with_gcps = process_orthomosaic(
            photos_dir=dataset_dirs,
            output_path=ortho_output_dir,
            project_path=project_path_with_gcps,
            gcp_file=gcp_file_for_processing,
            product_id="combined_with_gcps",
            clean_intermediate_files=False,
            photo_match_quality=PhotoMatchQuality.MediumQuality,
            depth_map_quality=DepthMapQuality.MediumQuality,
            tiepoint_limit=10000,
            use_gcps=True,
            gcp_accuracy=0.01  # Very low accuracy (1cm) for very high weight in bundle adjustment
        )
    
    print("\n✓ Combined orthomosaic processing (with GCPs) complete!")
    print(f"  Number of photos: {stats_with_gcps['num_photos']}")
    print(f"  Number of markers: {stats_with_gcps.get('num_markers', 0)}")
    print(f"  Orthomosaic: {stats_with_gcps['ortho_path']}")
    
    ortho_with_gcps_path = Path(stats_with_gcps['ortho_path'])
    
    # Post-processing: Compress existing large GeoTIFF files if they're not already compressed
    if ortho_with_gcps_path.exists():
        file_size_gb = ortho_with_gcps_path.stat().st_size / (1024 * 1024 * 1024)
        if file_size_gb > 1.0:  # If file is larger than 1GB, try to compress
            print(f"\n📦 File size is {file_size_gb:.2f} GB. Attempting post-processing compression...")
            try:
                import rasterio
                from rasterio.enums import Compression
                
                # Read the file
                with rasterio.open(ortho_with_gcps_path, 'r') as src:
                    data = src.read()
                    profile = src.profile.copy()
                
                # Update profile with LZW compression
                profile.update({
                    'compress': 'lzw',
                    'tiled': True,
                    'blockxsize': 512,
                    'blockysize': 512,
                })
                
                # Write compressed version to temporary file
                temp_path = ortho_with_gcps_path.with_suffix('.tif.tmp')
                with rasterio.open(temp_path, 'w', **profile) as dst:
                    dst.write(data)
                
                # Replace original with compressed version
                temp_path.replace(ortho_with_gcps_path)
                new_size_gb = ortho_with_gcps_path.stat().st_size / (1024 * 1024 * 1024)
                compression_ratio = (1 - new_size_gb / file_size_gb) * 100
                print(f"  ✓ Compression complete: {file_size_gb:.2f} GB → {new_size_gb:.2f} GB ({compression_ratio:.1f}% reduction)")
            except Exception as e:
                print(f"  ⚠️  Post-processing compression failed: {e}")
                print(f"  Note: File was exported with LZW compression from MetaShape, so it should already be compressed.")


Processing Combined Orthomosaic - WITH GCPs...
Combining images from:
  - DJI_202510060955_017_25-3288: 543 images
  - DJI_202510060955_018_25-3288: 865 images
  - DJI_202510060955_019_25-3288: 528 images
📁 Created temporary combined directory: /var/folders/45/msyhv5rs7xb6v19f926jmt_h0000gp/T/combined_images_ofdj731w


2025-12-02 17:44:48,839 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📝 MetaShape verbose output will be saved to: outputs/intermediate/logs/combined_with_gcps_metashape.log
2025-12-02 17:44:48,840 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📂 Loading existing project: outputs/intermediate/combined_with_gcps.psx


  ✓ Created 1936 symlinks in temporary directory
LoadProject: path = outputs/intermediate/combined_with_gcps.psx
loaded project in 0.012023 sec


Document.open(): The document is opened in read-only mode because it is already in use.


SaveProject: path = outputs/intermediate/combined_with_gcps.psx
saved project in 0.169558 sec
LoadProject: path = outputs/intermediate/combined_with_gcps.psx


...

BuildOrthomosaic: surface = Mesh, blending mode = Mosaic, fill holes = 1, ghosting filter = 0, cull faces = 0, refine seamlines = 0, resolution = 0
initializing...
tessellating mesh... done (90350834 -> 90350834 faces)
generating 104312x107947 orthomosaic (11 levels, 0.0118486 resolution)
selected 1935 cameras
saved orthomosaic data in 0.000761 sec
saved camera partition in 0.000744 sec
scheduled 97 orthophoto groups
loaded camera partition in 8.5e-05 sec
tessellating mesh... done (90350834 -> 90350834 faces)
loaded orthomosaic data in 10.1343 sec
Orthorectifying 20 images
DJI_20251006101512_0001: 8576x8873 -> 7089x6941
DJI_20251006101513_0002: 8576x8873 -> 7045x6983
DJI_20251006101515_0003: 11995x8873 -> 7001x7106
DJI_20251006101517_0004: 11995x10469 -> 7022x7083
DJI_20251006101519_0005: 10594x10469 -> 6964x7063
DJI_20251006101521_0006: 9268x9208 -> 8170x6914
DJI_20251006101523_0007: 12751x9213 -> 8335x7125
DJI_20251006101525_0008: 11595x12371 -> 8048x7060
DJI_20251006101527_0009: 102

2025-12-03 10:28:49,048 - qualicum_beach_gcp_analysis.metashape_processor - INFO - Exporting GeoTIFF to: outputs/orthomosaics/combined_with_gcps.tif
2025-12-03 10:28:49,050 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Full path: /Users/mauriciohessflores/Documents/Code/MyCode/research-westminster_ground_truth_analysis/outputs/orthomosaics/combined_with_gcps.tif
2025-12-03 10:28:49,053 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Output directory exists: True


ExportRaster: path = outputs/orthomosaics/combined_with_gcps.tif, description = Orthomosaic generated by Qualicum Beach GCP Analysis (with GCPs)
generating 104312 x 107946 raster in 1 x 1 tiles
SaveProject: path = outputs/intermediate/combined_with_gcps.psx
saved project in 0.001013 sec
LoadProject: path = outputs/intermediate/combined_with_gcps.psx
loaded project in 0.191616 sec


2025-12-03 10:33:48,436 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✓ GeoTIFF exported successfully!
2025-12-03 10:33:48,436 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   File: /Users/mauriciohessflores/Documents/Code/MyCode/research-westminster_ground_truth_analysis/outputs/orthomosaics/combined_with_gcps.tif
2025-12-03 10:33:48,436 - qualicum_beach_gcp_analysis.metashape_processor - INFO -   Size: 57424.89 MB
2025-12-03 10:33:48,438 - qualicum_beach_gcp_analysis.metashape_processor - INFO - ✅ MetaShape processing completed successfully
2025-12-03 10:33:48,438 - qualicum_beach_gcp_analysis.metashape_processor - INFO - 📄 Full verbose log saved to: outputs/intermediate/logs/combined_with_gcps_metashape.log



✓ Combined orthomosaic processing (with GCPs) complete!
  Number of photos: 1936
  Number of markers: 23
  Orthomosaic: outputs/orthomosaics/combined_with_gcps.tif


## Step 6: Process Combined Orthomosaic - WITHOUT GCPs

**Note**: This step is controlled by the `COMPUTE_NON_GCP_CASE` flag in Step 5. 
Set it to `True` to compute the orthomosaic without GCPs (takes a long time).
Currently set to `False` to skip this computation.


In [ ]:
# This step is now handled in Step 5 with the COMPUTE_NON_GCP_CASE flag
# If you need to run it separately, set COMPUTE_NON_GCP_CASE = True in Step 5 and re-run that cell
print("ℹ️  Non-GCP processing is controlled by COMPUTE_NON_GCP_CASE flag in Step 5.")
print("   Set COMPUTE_NON_GCP_CASE = True in Step 5 to compute the orthomosaic without GCPs.")


## Step 7: Download Reference Basemap

Download a reference basemap for comparison with the generated orthomosaics.


In [ ]:
# Calculate bounding box from GCPs for basemap download
# Check if required variables are defined
try:
    _ = min_x
    _ = min_y
    _ = max_x
    _ = max_y
except NameError:
    # Try to get bounds from GCP parser if available
    try:
        _ = gcp_parser
        min_x, min_y, max_x, max_y = gcp_parser.get_bounds()
        print(f"ℹ️  Retrieved GCP bounds from gcp_parser: X=[{min_x:.2f}, {max_x:.2f}], Y=[{min_y:.2f}, {max_y:.2f}]")
    except NameError:
        # Try to load GCPs from file
        try:
            _ = data_dir
        except NameError:
            data_dir = Path("/Users/mauriciohessflores/Documents/Code/Data/New Westminster Oct _25")
        
        try:
            _ = gcp_file
        except NameError:
            gcp_file = data_dir / "25-3288-CONTROL-NAD83-UTM10N-EGM2008.csv"
        
        # Load GCPs to get bounds
        import csv
        import utm
        gcps_utm = []
        with open(gcp_file, 'r') as f:
            reader = csv.DictReader(f)
            for row in reader:
                try:
                    x = float(row.get('X', row.get('x', 0)))
                    y = float(row.get('Y', row.get('y', 0)))
                    gcps_utm.append({'x': x, 'y': y})
                except:
                    continue
        
        if gcps_utm:
            min_x = min(g['x'] for g in gcps_utm)
            max_x = max(g['x'] for g in gcps_utm)
            min_y = min(g['y'] for g in gcps_utm)
            max_y = max(g['y'] for g in gcps_utm)
            print(f"ℹ️  Calculated GCP bounds: X=[{min_x:.2f}, {max_x:.2f}], Y=[{min_y:.2f}, {max_y:.2f}]")
        else:
            raise ValueError("Could not determine GCP bounds")

# Convert UTM bounds to lat/lon
center_easting = (min_y + max_y) / 2  # Y column is easting
center_northing = (min_x + max_x) / 2  # X column is northing
lat_center, lon_center = utm.to_latlon(center_easting, center_northing, 10, 'N')

# Convert bounds
lat_min, lon_min = utm.to_latlon(min_y, min_x, 10, 'N')
lat_max, lon_max = utm.to_latlon(max_y, max_x, 10, 'N')

# Add padding
padding = 0.001
bbox = (lat_min - padding, lon_min - padding, lat_max + padding, lon_max + padding)

print(f"Basemap bounding box: {bbox}")

# Import download function
try:
    from qualicum_beach_gcp_analysis import download_basemap
except ImportError:
    try:
        from westminster_ground_truth_analysis import download_basemap
    except ImportError:
        print("⚠️  download_basemap function not available. Please install qualicum_beach_gcp_analysis package.")
        download_basemap = None

if download_basemap:
    # Check if output_dir is defined
    try:
        _ = output_dir
    except NameError:
        output_dir = Path("outputs")
    
    # Download basemap
    basemap_path = download_basemap(
        bbox=bbox,
        output_path=str(output_dir / "basemap.tif"),
        source="esri_world_imagery",
        target_resolution=0.1  # 0.1m per pixel
    )
    
    print(f"\n✓ Basemap saved to: {basemap_path}")
else:
    print("⚠️  Cannot download basemap - download_basemap function not available")


## Step 8: Compare Orthomosaics to Basemap

Compare the generated orthomosaics (with and/or without GCPs) to the reference basemap.


In [ ]:
# Compare orthomosaics to basemap
# Import comparison function
try:
    from qualicum_beach_gcp_analysis import compare_orthomosaic_to_basemap
except ImportError:
    try:
        from westminster_ground_truth_analysis import compare_orthomosaic_to_basemap
    except ImportError:
        print("⚠️  compare_orthomosaic_to_basemap function not available.")
        compare_orthomosaic_to_basemap = None

if not compare_orthomosaic_to_basemap:
    print("⚠️  Cannot compare orthomosaics - function not available")
else:
    # Setup paths
    try:
        _ = output_dir
    except NameError:
        output_dir = Path("outputs")
    
    comparison_dir = output_dir / "comparisons"
    comparison_dir.mkdir(exist_ok=True)
    
    # Determine orthomosaic paths (combined dataset)
    ortho_output_dir = output_dir / "orthomosaics"
    ortho_no_gcps_path = ortho_output_dir / "combined_no_gcps.tif"
    ortho_with_gcps_path = ortho_output_dir / "combined_with_gcps.tif"
    
    # Check if paths were defined in Step 5
    try:
        _ = ortho_with_gcps_path
        if 'ortho_with_gcps_path' in locals() and isinstance(ortho_with_gcps_path, Path):
            ortho_with_gcps_path = ortho_with_gcps_path
    except:
        pass
    
    try:
        _ = ortho_no_gcps_path
        if 'ortho_no_gcps_path' in locals() and isinstance(ortho_no_gcps_path, Path):
            ortho_no_gcps_path = ortho_no_gcps_path
    except:
        pass
    
    print("=" * 60)
    print("Comparing orthomosaics to basemap...")
    print("=" * 60)
    
    # Ensure basemap_path is a Path object
    if isinstance(basemap_path, str):
        basemap_path = Path(basemap_path)
    
    # Compare Combined - Without GCPs
    metrics_no_gcps = {}
    if ortho_no_gcps_path.exists():
        print("\nCombined Orthomosaic - Without GCPs")
        print("-" * 60)
        metrics_no_gcps = compare_orthomosaic_to_basemap(
            Path(ortho_no_gcps_path),
            Path(basemap_path),
            output_dir=comparison_dir / "combined_no_gcps"
        )
    else:
        print(f"\n⚠️  Orthomosaic not found: {ortho_no_gcps_path}")
        print("   (This is expected if COMPUTE_NON_GCP_CASE=False in Step 5)")
    
    # Compare Combined - With GCPs
    metrics_with_gcps = {}
    if ortho_with_gcps_path.exists():
        print("\nCombined Orthomosaic - With GCPs")
        print("-" * 60)
        metrics_with_gcps = compare_orthomosaic_to_basemap(
            Path(ortho_with_gcps_path),
            Path(basemap_path),
            output_dir=comparison_dir / "combined_with_gcps"
        )
    else:
        print(f"\n⚠️  Orthomosaic not found: {ortho_with_gcps_path}")
    
    print("\n✓ All comparisons complete!")


## Step 9: Generate Quality Report

Generate a comprehensive quality report comparing the orthomosaics.


In [ ]:
# Create comparison summary
import pandas as pd
import matplotlib.pyplot as plt

# Helper function to safely get metrics
def get_metric(metrics_dict, key, default=0.0):
    """Safely get a metric value, handling different key formats."""
    if not metrics_dict:
        return default
    # Try overall key first
    if 'overall' in metrics_dict:
        overall = metrics_dict['overall']
        if key in overall:
            return overall[key]
        # Try with _pixels suffix
        if f"{key}_pixels" in overall:
            return overall[f"{key}_pixels"]
    # Try direct key
    if key in metrics_dict:
        return metrics_dict[key]
    # Try with _pixels suffix
    if f"{key}_pixels" in metrics_dict:
        return metrics_dict[f"{key}_pixels"]
    return default

# Collect metrics (only include available orthomosaics)
summary_data = {
    'Configuration': [],
    'GCPs Used': [],
    'RMSE': [],
    'MAE': [],
    'Similarity': [],
    'Seamlines (%)': [],
    'Displacement (pixels)': [],
    'Num Matches': [],
}

# Add metrics for orthomosaic without GCPs if available
if metrics_no_gcps:
    summary_data['Configuration'].append('Combined')
    summary_data['GCPs Used'].append('No')
    summary_data['RMSE'].append(get_metric(metrics_no_gcps, 'rmse'))
    summary_data['MAE'].append(get_metric(metrics_no_gcps, 'mae'))
    summary_data['Similarity'].append(get_metric(metrics_no_gcps, 'similarity'))
    summary_data['Seamlines (%)'].append(get_metric(metrics_no_gcps, 'seamline_percentage'))
    errors_2d = metrics_no_gcps.get('overall', {}).get('errors_2d', {})
    summary_data['Displacement (pixels)'].append(errors_2d.get('rmse_2d_pixels', 0.0))
    summary_data['Num Matches'].append(errors_2d.get('num_matches', 0))

# Add metrics for orthomosaic with GCPs if available
if metrics_with_gcps:
    summary_data['Configuration'].append('Combined')
    summary_data['GCPs Used'].append('Yes')
    summary_data['RMSE'].append(get_metric(metrics_with_gcps, 'rmse'))
    summary_data['MAE'].append(get_metric(metrics_with_gcps, 'mae'))
    summary_data['Similarity'].append(get_metric(metrics_with_gcps, 'similarity'))
    summary_data['Seamlines (%)'].append(get_metric(metrics_with_gcps, 'seamline_percentage'))
    errors_2d = metrics_with_gcps.get('overall', {}).get('errors_2d', {})
    summary_data['Displacement (pixels)'].append(errors_2d.get('rmse_2d_pixels', 0.0))
    summary_data['Num Matches'].append(errors_2d.get('num_matches', 0))

if summary_data['Configuration']:
    df = pd.DataFrame(summary_data)
    
    print("\n" + "=" * 60)
    print("SUMMARY COMPARISON")
    print("=" * 60)
    print(df.to_string(index=False))
    
    # Save summary to CSV
    try:
        _ = output_dir
    except NameError:
        output_dir = Path("outputs")
    
    summary_csv = output_dir / "quality_summary.csv"
    df.to_csv(summary_csv, index=False)
    print(f"\n✓ Summary saved to: {summary_csv}")
    
    # Create visualizations
    available_metrics = []
    for col in ['RMSE', 'MAE', 'Similarity', 'Seamlines (%)', 'Displacement (pixels)', 'Num Matches']:
        if col in df.columns and df[col].sum() > 0:
            available_metrics.append(col)
    
    if available_metrics:
        n_metrics = len(available_metrics)
        n_cols = min(3, n_metrics)
        n_rows = (n_metrics + n_cols - 1) // n_cols
        
        fig, axes = plt.subplots(n_rows, n_cols, figsize=(6*n_cols, 5*n_rows))
        if n_metrics == 1:
            axes = [axes]
        else:
            axes = axes.flatten() if n_rows > 1 else [axes] if n_cols == 1 else axes
        
        for i, metric in enumerate(available_metrics):
            ax = axes[i]
            df_pivot = df.pivot(index='Configuration', columns='GCPs Used', values=metric)
            df_pivot.plot(kind='bar', ax=ax, rot=0)
            ax.set_title(metric)
            ax.set_ylabel('Value')
            ax.legend(title='GCPs Used')
            ax.grid(True, alpha=0.3)
        
        # Hide unused subplots
        for i in range(len(available_metrics), len(axes)):
            axes[i].axis('off')
        
        plt.tight_layout()
        report_plot_path = output_dir / "quality_report.png"
        plt.savefig(report_plot_path, dpi=150, bbox_inches='tight')
        print(f"✓ Quality report plot saved to: {report_plot_path}")
        plt.show()
    else:
        print("⚠️  No metrics available for visualization")
    
    # Generate markdown report
    report_md = output_dir / "quality_report.md"
    with open(report_md, 'w') as f:
        f.write("# Westminster Ground Truth Analysis - Quality Report\n\n")
        f.write("## Summary\n\n")
        f.write(df.to_markdown(index=False))
        f.write("\n\n## Findings\n\n")
        if metrics_no_gcps:
            f.write("### Combined Orthomosaic - Without GCPs\n")
            f.write(f"- **RMSE**: {get_metric(metrics_no_gcps, 'rmse'):.3f}\n")
            f.write(f"- **MAE**: {get_metric(metrics_no_gcps, 'mae'):.3f}\n")
            f.write(f"- **Similarity**: {get_metric(metrics_no_gcps, 'similarity'):.4f}\n")
            f.write(f"- **Seamlines**: {get_metric(metrics_no_gcps, 'seamline_percentage'):.2f}%\n")
            errors_2d = metrics_no_gcps.get('overall', {}).get('errors_2d', {})
            f.write(f"- **Displacement**: {errors_2d.get('rmse_2d_pixels', 0.0):.2f} pixels\n")
            f.write(f"- **Num Matches**: {errors_2d.get('num_matches', 0)}\n\n")
        if metrics_with_gcps:
            f.write("### Combined Orthomosaic - With GCPs\n")
            f.write(f"- **RMSE**: {get_metric(metrics_with_gcps, 'rmse'):.3f}\n")
            f.write(f"- **MAE**: {get_metric(metrics_with_gcps, 'mae'):.3f}\n")
            f.write(f"- **Similarity**: {get_metric(metrics_with_gcps, 'similarity'):.4f}\n")
            f.write(f"- **Seamlines**: {get_metric(metrics_with_gcps, 'seamline_percentage'):.2f}%\n")
            errors_2d = metrics_with_gcps.get('overall', {}).get('errors_2d', {})
            f.write(f"- **Displacement**: {errors_2d.get('rmse_2d_pixels', 0.0):.2f} pixels\n")
            f.write(f"- **Num Matches**: {errors_2d.get('num_matches', 0)}\n\n")
    
    print(f"✓ Markdown report saved to: {report_md}")
else:
    print("⚠️  No orthomosaics available for comparison. Please run Steps 5-8 first.")
